In [111]:
import networkx as nx
import pandas as pd
import pickle
import time
import numpy as np
from datetime import datetime
import matplotlib.pyplot as plt

In [127]:
df = pd.read_csv('./Data/HI-Small_Trans.csv')
dates = pd.to_datetime(df["Timestamp"])
out  = (dates - pd.Timestamp("1970-01-01")) // pd.Timedelta('1s')
# change time to unix
df["Timestamp"] = out - out.min()
# drop a few rows so we can reduce edge dimensionality
df = df.drop(df[df["Receiving Currency"] != df["Payment Currency"]].index)

2022-09-18 16:18:00
1663517880


In [53]:
start_time = time.time()
graph = nx.MultiDiGraph()

edge_features = ['Timestamp', 'Amount Paid', 'Payment Currency', 'Payment Format']

for i, row in df.iterrows():
    source_node = row['Account'] + str(row['From Bank'])
    target_node = row['Account.1'] + str(row['To Bank'])

    graph.add_edge(source_node, target_node, timestamp=row["Timestamp"], amount_paid=row["Amount Paid"], payment_currency=row["Payment Currency"], payment_format=row["Payment Format"])
    if i % 500000 == 0:
        print("Done: ", i / 1000000, " million")
elapsed_time = time.time() - start_time
print(f'Graph creation took {elapsed_time:.3f} seconds')

Done:  0.0  million
Done:  0.5  million
Done:  1.0  million
Done:  1.5  million
Done:  2.0  million
Done:  3.0  million
Done:  3.5  million
Done:  4.0  million
Done:  4.5  million
Done:  5.0  million
Graph creation took 414.826 seconds


In [54]:
# save graph object to file
filename ="1dNode_4dEdge_HI_SMALL"
pickle.dump(graph, open(filename + '.pickle', 'wb'))

In [55]:
# load graph object from file
filename ="1dNode_4dEdge_HI_SMALL"
G = pickle.load(open(filename + '.pickle', 'rb'))

In [132]:
import numpy as np
# len(G.nodes), len(G.edges)
# plt.hist(df["Timestamp"], bins=100)
# plt.show()

NodeView(('8000EBD3010', '8000F45803208', '8000F53401', '8000F46703209', '8000F503012', '8000F520010', '8000F5AD01', '8000EBAC01', '8000EC1E01', '8000EC28012', '8017BF8002439', '8000EDEC01', '80AEF5310211050', '8000F45101', '8011305D011813', '8000F47F01', '8000F4FE01', '812ED62E0245335', '80012FD9010', '812ED638036056', '80012FE0012', '805B3421013037', '80012FE501', '80012FEA010', '8005DFEB01420', '8005E18F01665', '8005E24C01665', '8005F2D301420', '80013148010', '800131B1012', '8131A9A8011642', '8005F0B5010', '810B0FB4013327', '8005FB700908', '813600910143995', '8005FD3901420', '8005FD4301688', '800A5F0201', '8006A38401420', '8006A38901292', '8006AF50010', '8006AF55031125', '80005810010', '80C132DC0217680', '80A3C7390121303', '800AC8E301674', '800AC901021611', '800ACA9C011157', '8010083401467', '8010085201420', '80005D5C010', '800AC8E8011296', '800AC940011474', '814233CC01124', '800AC9DD01601', '8121CF4B0215064', '800AC9E201411', '8082250C0111764', '8010084801241', '8065002B015723', '8

In [99]:
F = nx.DiGraph(G)
F.number_of_nodes(), len(F.edges)

(515047, 1011926)